<a href="https://colab.research.google.com/github/Avipsa1/UPPP275-Notebooks/blob/main/Adding_a_web_basemap_using_Folium.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Adding a web basemap using Folium

<font size="4">The idea of using `Folium` is to add a web basemap to give your map visulization a little more context. For example, if you present your Phoenix crime map to someone who are not familiar with Phoenix, they might get lost about where is where. So, by adding a basemap such as Google Maps or OpenStreetMap, it will make much easier for the person who is reading your map.</font>

<br></br>
<font size="4">First of all, let's get a feel about it!</font>

In [1]:
import folium

<br></br>
<font size="4">`folium.Map()`  gives us the basemap at a given location. In this example, I use a location with longitude of -111.9400 and latitude of 33.4255. </font>

In [5]:
folium.Map(location=[33.6694, -117.8230])

In [3]:
help(folium.Map)

Help on class Map in module folium.folium:

class Map(branca.element.MacroElement)
 |  Map(location=None, width='100%', height='100%', left='0%', top='0%', position='relative', tiles='OpenStreetMap', API_key=None, max_zoom=18, min_zoom=0, max_native_zoom=None, zoom_start=10, world_copy_jump=False, no_wrap=False, attr=None, min_lat=-90, max_lat=90, min_lon=-180, max_lon=180, max_bounds=False, detect_retina=False, crs='EPSG3857', control_scale=False, prefer_canvas=False, no_touch=False, disable_3d=False, subdomains='abc', png_enabled=False, zoom_control=True)
 |  
 |  Create a Map with Folium and Leaflet.js
 |  
 |  Generate a base map of given width and height with either default
 |  tilesets or a custom tileset URL. The following tilesets are built-in
 |  to Folium. Pass any of the following to the "tiles" keyword:
 |  
 |      - "OpenStreetMap"
 |      - "Mapbox Bright" (Limited levels of zoom for free tiles)
 |      - "Mapbox Control Room" (Limited levels of zoom for free tiles)
 |  

<br></br>
<font size="4">There are many parameters in the `folium.Map()` method. For example, besides location, we can specify the 
style of the map, the zoom level and the size of the map.</font>

In [14]:
uci = folium.Map(
    location=[33.64217, -117.84566],
    tiles='Stamen Toner',
    zoom_start=15,
    width=1000, 
    height=400
)
uci

<br></br>
<font size="4">We can also add some markers to the asu map by using `folium.Marker().add_to(asu)`. Here, I added two locations on campus.</font>

In [15]:
folium.Marker([33.64717, -117.84495], popup='<i>ALP</i>').add_to(uci)
folium.Marker([33.64608, -117.84295], popup='<b>Aldrich Park</b>').add_to(uci)
uci

<br></br>
<font size="4">How about overlaying our Phoenix Crime Map? Let's read in our `phoenix_crime_counts.shp`.</font>

In [ ]:
import geopandas as gpd
phx_crimes = gpd.read_file("../Data/phoenix_crime_counts/phoenix_crime_counts.shp")

In [ ]:
phx_crimes.crs

{'init': 'epsg:4269'}

<br></br>
<font size="4">Remember our origin projection is latitude and longitude ('epsg:4269'), and We need to convert it to the web mercator which is 'epsg:4326'. It is very important to let your GeoDataFrame to have the web mercator projection in order to be displayed properly.</font>

<br></br>
<font size="4">Next we need to use `.to_json` command to convert the `GeoDataFrame` to the `geojson` format that `folium` supports.</font>

In [ ]:
phx_crimes_json = phx_crimes.to_crs(epsg='4326').to_json()

<br></br>
<font size="4">Let's create a basemap first with proper zoom-level (feel free to play around with the zoom-level).</font>

In [ ]:
crime_map = folium.Map(location=[33.4255, -111.9400], zoom_start=9)

<br></br>
<font size="4">Then we need to use the `geojson` file to make a `folium.Choropleth` Map. Below are the commands.</font>

In [ ]:
folium.Choropleth(
    geo_data=phx_crimes_json,
    name='Phoenix Crime Counts', # 
    data=phx_crimes, #Our GeoDataFrame
    columns=['Zipcode','INC NUMBER'], #
    key_on='feature.properties.{}'.format('Zipcode'), #we need to specify a unique key for each zipcode
    fill_color='RdBu_r', #fill color, here I'm using blue to red
    fill_opacity=0.7, # opacity of the polygon fill color
    line_opacity=0.2, # opacity of the boundary line
    legend_name='counts', #legend name
    highlight = True, #Hover to highlight
    control = True
).add_to(crime_map)

crime_map

<br></br>
<font size="4">We can also add a `folium.LayerControl()` to our `crime_map` so that we can toggle layers. Note there will be small button on the top-left corner of your map.</font>

In [ ]:
folium.LayerControl().add_to(crime_map)
crime_map

<br></br>
<font size="4">Finally, this can also be saved as a html webpage.</font>

In [ ]:
crime_map.save('phx_crime_map_folium.html')